In [159]:
# Load libraries
import pandas as pd
from sklearn.tree import DecisionTreeClassifier # Import Decision Tree Classifier
from sklearn.model_selection import train_test_split # Import train_test_split function
from sklearn import metrics #Import scikit-learn metrics module for accuracy calculation
from sklearn.model_selection import GridSearchCV
import numpy as np

In [198]:
# Load the dataset
data = pd.read_csv("cleaned_data/cleaned_asylum_seekers_added.csv")
data = data[data['HDI'] != '..']
data = data.dropna()
decimals = 2    
data['Unemployment rate'] = data['Unemployment rate'].apply(lambda x: round(x, decimals))
data['origin_to_target_dist'] = data['origin_to_target_dist'].apply(lambda x: round(x, decimals))
data.head()
 

C:\Users\LM\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3020: DtypeWarning: Columns (19) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Year Country / territory of asylum/residence   Origin  \
0  2001                            South Africa   Angola   
1  2001                            South Africa   Angola   
2  2001                            South Africa  Albania   
3  2001                            South Africa  Burundi   
4  2001                            South Africa  Burundi   

  RSD procedure type / level  decisions_recognized  decisions_other  Rejected  \
0                     G / AR                   0.0              0.0       0.0   
1                     G / FI                 860.0              0.0      36.0   
2                     G / AR                   0.0              0.0       0.0   
3                     G / AR                   0.0              0.0       0.0   
4                     G / FI                 808.0              0.0     234.0   

   Otherwise_closed  Total decisions  Successful      ...        \
0               1.0              0.0         0.0      ...         
1              68.0            964.0       860.0      ...         
2               1.0              0.0         0.0      ...         
3               1.0              0.0         0.0      ...         
4               7.0           1049.0       808.0      ...         

   Origin_latitude  Origin_longitude  origin_to_target_dist   HDI  \
0       -14.270972       -170.132217               11214.77  0.61   
1       -14.270972       -170.132217               11214.77  0.61   
2        41.153332         20.168331               11919.88  0.61   
3        12.238333         -1.561593                8114.66  0.61   
4        12.238333         -1.561593                8114.66  0.61   

   Unemployment rate  acceptance_rate  accepted/rejected  \
0               30.9         0.000000                  0   
1               30.9         0.892116                  3   
2               30.9         0.000000                  0   
3               30.9         0.000000                  0   
4               30.9         0.770257                  3   

   Encoded procedure type  Encoded Target Country Encoded Origin  
0                       1                     135              3  
1                       6                     135              3  
2                       1                     135              1  
3                       1                     135             25  
4                       6                     135             25  

[5 rows x 26 columns]

In [110]:
params_dt = {
             'max_depth': [2, 3, 4],
             'min_samples_leaf': [0.12, 0.14, 0.16, 0.18]
            }
'HDI','Unemployment rate','GDP_difference','origin_to_target_dist','Encoded Origin', 'Encoded Target Country'

('HDI',
 'Unemployment rate',
 'GDP_difference',
 'origin_to_target_dist',
 'Encoded Origin',
 'Encoded Target Country')

In [219]:
col_names = [   'Unemployment rate','Encoded Target Country', 'Encoded procedure type'] # Declare the columns names

x = data[col_names] # 
y = data['accepted/rejected'] # Target Variable

In [220]:
# Split dataset into training set and test set
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=1) # 70% training and 30% test

In [221]:
# Create Decision Tree classifer object
clf = DecisionTreeClassifier()

print ( clf.get_params())

# Train Decision Tree Classifer
clf = clf.fit(x_train,y_train)

#Predict the response for test dataset
y_pred = clf.predict(x_test)

{'class_weight': None, 'criterion': 'gini', 'max_depth': None, 'max_features': None, 'max_leaf_nodes': None, 'min_impurity_decrease': 0.0, 'min_impurity_split': None, 'min_samples_leaf': 1, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'presort': False, 'random_state': None, 'splitter': 'best'}


In [222]:
grid_dt = GridSearchCV(estimator=clf,
                       param_grid=params_dt,
                       scoring='roc_auc',
                       cv=5,
                       n_jobs=-1)
grid_dt.fit(x_train, y_train )

# Import roc_auc_score from sklearn.metrics 
from sklearn.metrics import roc_auc_score

# Extract the best estimator
best_model = grid_dt.best_estimator_

# Predict the test set probabilities of the positive class
y_pred_proba = best_model.predict_proba(X_test)[:,1]

# Compute test_roc_auc
test_roc_auc = roc_auc_score(y_test, y_pred_proba)

# Print test_roc_auc
print('Test set ROC AUC score: {:.3f}'.format(test_roc_auc))

ValueError: multiclass format is not supported

In [223]:
# Model Accuracy, how often is the classifier correct?
print("Accuracy:",metrics.accuracy_score(y_test, y_pred))

#print("Accuracy:",metrics.precision_score(y_test, y_pred, average='samples'))
print(metrics.classification_report(y_test, y_pred, target_names=['0','1','2','3']))
df=pd.DataFrame({'Actual':y_test, 'Predicted':y_pred})
df

Accuracy: 0.8214810731348768
              precision    recall  f1-score   support

           0       0.83      0.99      0.90     26743
           1       0.31      0.02      0.04      3466
           2       0.24      0.03      0.05      1416
           3       0.60      0.20      0.30      1027

   micro avg       0.82      0.82      0.82     32652
   macro avg       0.49      0.31      0.33     32652
weighted avg       0.74      0.82      0.76     32652



Actual  Predicted
54282        0          0
74594        0          0
96300        0          0
44548        0          0
80242        0          0
62296        0          0
42370        0          0
9014         0          0
85790        0          0
63403        2          0
16934        0          0
25932        0          0
86151        0          0
77537        0          0
73124        2          0
98486        0          0
73110        0          0
106027       0          0
79948        1          0
54974        1          0
92383        2          0
18914        0          0
26713        0          0
24164        2          0
26226        1          0
90867        0          0
14738        0          0
106051       0          0
9102         0          0
25975        0          0
...        ...        ...
50591        1          0
43466        0          0
55227        1          0
71965        0          0
15234        0          0
10582        0          0
37904        0          0
51236        0          0
85537        0          0
89500        1          0
12857        0          0
86522        0          0
59190        0          0
29404        0          0
46709        0          0
21797        3          0
32569        1          0
68023        0          0
36916        0          0
20196        0          0
20743        0          0
63165        0          0
87092        0          0
35720        0          0
55075        1          0
81680        0          0
3038         1          0
50076        0          0
40834        0          0
93033        0          0

[32652 rows x 2 columns]

In [84]:
from sklearn.tree import export_graphviz
from sklearn.externals.six import StringIO  
from IPython.display import Image  
import pydotplus

dot_data = StringIO()
export_graphviz(clf, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True,feature_names = col_names,class_names=['0','1','2','3'])
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.805007 to fit

